# midi_procesing

In [1]:
import os
import sys
import pickle
import numpy as np
from collections import defaultdict
from random import randint

import pretty_midi as pm
from tqdm import tqdm

In [1]:
TODO = '''
'''

In [2]:
def get_bar_indexes_with_content(bars):
    '''this method is looking for non-empty bars in the tracks bars
    the empty bar consist of only rest notes.
    returns: a set of bars indexes with notes
    '''
    bars_indexes_with_content = set()
    for i, bar in enumerate(bars):
        if bar_has_content(bar):
            bars_indexes_with_content.add(i)

    return bars_indexes_with_content    

In [3]:
def get_bars_with_content(bars):
    '''this method is looking for non-empty bars in the tracks bars
    the empty bar consist of only rest notes.
    returns: a set of bars with notes
    '''
    bars_with_content = []
    for bar in bars:
        if bar_has_content(bar):
            bars_with_content.append(bar)

    return bars_with_content  

In [4]:
def get_common_bars(track_x,track_y):
    '''return common bars, for two tracks is song
    return X_train, y_train list of 
    '''
    bars_x = track_x.stream_to_bars()
    bars_y = track_y.stream_to_bars()
    bwc_x = get_bar_indexes_with_content(bars_x)
    bwc_y = get_bar_indexes_with_content(bars_y)

    common_bars = bwc_x.intersection(bwc_y)
    common_bars_x = [bars_x[i] for i in common_bars]
    common_bars_y = [bars_y[i] for i in common_bars]
    return common_bars_x, common_bars_y

In [5]:
def get_bar_len(bar):
    """calculate a lenth of a bar
    parameters:
        bar : list
            list of "notes", tuples like (pitches, len)
    """
    time = 0
    for note in bar:
        time += note[1]
    return time

In [6]:
def bar_has_content(bar):
    '''check if bar has any musical information, more accurate
    it checks if in a bar is any non-rest event like note, or chord
    
    parameters:
    -----------
        bar: list
            list of notes
            
    return:
    -------
        bool:
            True if bas has concent and False of doesn't
    '''
    bar_notes = len(bar)
    count_rest = 0
    for note in bar:
        if note[0] == (-1,):
            count_rest += 1
    if count_rest == bar_notes:
        return False
    else:
        return True

In [7]:
def round_to_sixteenth_note(x, base=0.25):
        '''round value to closest multiplication by base
        in default to 0.25 witch is sisteenth note accuracy 
        '''
        
        return base * round(x/base)

In [8]:
def parse_pretty_midi_instrument(instrument, resolution, time_to_tick, key_offset):
    ''' arguments: a prettyMidi instrument object
        return: a custom SingleTrack object
    '''
    
    # FIXME: there is a problem, where note is longer that bar and negative time occured
    # split note to max_rest_note
    
    first_tick = None
    prev_tick = 0
    prev_note_lenth = 0
    max_rest_len = 4.0

    notes = defaultdict(lambda:[set(), set()])
    for note in instrument.notes:
        if first_tick == None:
#             first_tick = round_to_sixteenth_note(time_to_tick(note.start)/resolution)
            first_tick = 0
            
        tick = round_to_sixteenth_note(time_to_tick(note.start)/resolution)
        # add rest if is a gap between last note end and next note start
        if prev_tick != None:
            act_tick = prev_tick + prev_note_lenth
            if act_tick < tick:
                rest_lenth = tick - act_tick
                while rest_lenth > max_rest_len:
                    notes[act_tick] = [{-1},{max_rest_len}]
                    act_tick += max_rest_len
                    rest_lenth -= max_rest_len
                notes[act_tick] = [{-1},{rest_lenth}]

        note_lenth = round_to_sixteenth_note(time_to_tick(note.end-note.start)/resolution)
        
        if -1 in notes[tick][0]:
            notes[tick] = [set(), set()]
        
        if instrument.is_drum:
            notes[tick][0].add(note.pitch)
        else:
            notes[tick][0].add(note.pitch+key_offset)
            
        # FIXME: trim notes, when longer then one bar lenth
        notes[tick][1].add(note_lenth)

        prev_tick = tick
        prev_note_lenth = note_lenth
    
    notes = [(tuple(e[0]), max(e[1])) for e in notes.values()]

    name = 'Drums' if instrument.is_drum else pm.program_to_instrument_class(instrument.program)
    return SingleTrack(name, instrument.program, instrument.is_drum, Stream(first_tick,notes) )

In [9]:
def remove_duplicated_sequences(xy_tuple):
    ''' removes duplicated x,y sequences
    parameters:
    -----------
        xy_tuple: tuple of lists
            tuple of x,y lists that represens sequances in training set
            
    return:
    ------
        x_unique, y_unique: tuple
            a tuple of cleaned x, y traing set
    '''
    x = xy_tuple[0]
    y = xy_tuple[1]
    x_freeze = [tuple(seq) for seq in x]
    y_freeze = [tuple(seq) for seq in y]
    unique_data = list(set(zip(x_freeze,y_freeze)))
    x_unique = [seq[0] for seq in unique_data]
    y_unique = [seq[1] for seq in unique_data]
    return x_unique, y_unique

In [10]:
# TODO: Stream class is no logner needed <- remore from code and make just SingleTrack.notes instead on SingleTrack.stream.notes
class Stream():
    
    def __init__ (self, first_tick, notes):
        self.notes = notes
        self.first_tick = first_tick
        
    def __repr__(self):
        return '<Stream object with {} musical events>'.format(len(self.notes))

In [11]:
class SingleTrack():
    '''class of single track in midi file encoded from pretty midi library
    
    atributes:
    ----------
        name:  str
            name of instrument class
        program: int
            midi instrument program
        is_drum: bool
            True if this track is drums track, False otherwise
        stream:
            Stream object of encoded music events (chords or notes)
    '''
    
    def __init__(self, name=None, program=None, is_drum=None, stream=None):
        self.name = name
        self.program = program
        self.is_drum = is_drum
        self.stream = stream
        self.is_melody = self.check_if_melody()
        
    def __repr__(self):
        return "<SingleTrack object. Name:{}, Program:{}, is_drum:{}>".format(self.name, self.program, self.is_drum)
    
    def to_pretty_midi_instrument(self, tempo=100):
        '''is create a pretty midi Instrument object from self.stream.notes sequance
           
            parameters: 
            -----------
                self: SingleTrack object
                
            return: 
            -------
                track: PrettyMIDI.Instrument object
        '''
        
        tempo_strech = 100/tempo
        track = pm.Instrument(program=self.program, is_drum=self.is_drum, name=self.name)
        time = self.stream.first_tick * tempo_strech
        for note in self.stream.notes:
            note_pitch = note[0]
            note_len = note[1] * tempo_strech
            for pitch in note_pitch:
                # if note is a rest (pause)
                if pitch == -1:
                    break
                event = pm.Note(velocity=100, pitch=pitch, start=time, end=time+note_len)
                track.notes.append(event)
            time = time + note_len

        return track
    
    def stream_to_bars(self, beat_per_bar=4):
        '''it takes notes and split it into equaly time distibuted sequances
        if note is between bars, the note is splited into two notes, with time sum equal to the note between bars.
        
        arguments:
        ----------
            stream: list of "notes"
            
        return:
        -------
            bars: list: list of lists of notes, every list has equal time. in musical context it returns bars
        '''
        # TODO: if last bar of sequance has less notes to has time equal given bar lenth it is left shorter
        # fill the rest of bar with rests
        
        # FIXME: there is a problem, where note is longer that bar and negative time occured
        # split note to max_rest_note, the problem occured when note is longer then 2 bars
        
        notes = self.stream.notes
        bars = []
        time = 0
        bar_index = 0
        add_tail = False
        note_pitch = lambda note: note[0]
        note_len = lambda note: note[1]
        for note in notes:
            try:
                temp = bars[bar_index]
            except IndexError:
                bars.append([])
                
            if add_tail:
                tail_pitch = note_pitch(tail_note)
                while tail_note_len > beat_per_bar:
                    bars[bar_index].append((tail_pitch, beat_per_bar))
                    tail_note_len -= beat_per_bar
                    bar_index += 1
                    bars.append([])
                       
                bars[bar_index].append((tail_pitch, tail_note_len))
                time += tail_note_len
                add_tail = False

            time += note_len(note)

            if time == beat_per_bar:
                bars[bar_index].append(note)
                time = 0
                bar_index += 1

            elif time > beat_per_bar: # if note is between bars
                between_bars_note_len =  note_len(note)
                tail_note_len = time - beat_per_bar
                leading_note_len = between_bars_note_len - tail_note_len
                
                leading_note = (note_pitch(note), leading_note_len)
                bars[bar_index].append(leading_note)
                tail_note = (note_pitch(note), tail_note_len)

                add_tail = True
                time = 0
                bar_index += 1
            else:
                bars[bar_index].append(note)
                
        return bars
    
    def check_if_melody(self):
        events = None
        single_notes = None
        for note in self.stream.notes:
            if self.name not in ['Bass','Drums']:
                events = 0
                single_notes = 0
                if note[0][0] != -1: # if note is not a rest
                    events += 1
                    if len(note[0]) == 1: # if note is a single note, not a chord
                        single_notes += 1

        if events != None:
            if events == 0:
                return False
            else:
                single_notes_rate = single_notes/events
                if single_notes_rate >= 0.9:
                    self.name = 'Melody'
                    return True
                else:
                    return False
        else:
            return False

In [12]:
class MultiTrack():
    '''Class that represent one midi file
    atributes:
        pm_obj : PrettyMIDI class object of this midi file
        res: resolution of midi
        time_to_tick: function that coverts miliseconds to ticks. it depends on midi resolution for every midi
        name: path to midi file
        tracks: a list of SingleTrack objects
    '''
    
    def __init__(self, path=None, tempo=100):
        self.tempo = tempo
        self.pm_obj = pm.PrettyMIDI(path, initial_tempo=self.tempo) # changename to self.PrettyMIDI
        self.res = self.pm_obj.resolution
        self.time_to_tick = self.pm_obj.time_to_tick
        self.name = path
        self.tracks = [parse_pretty_midi_instrument(instrument, self.res, self.time_to_tick, self.get_pitch_offset_to_C() ) for instrument in self.pm_obj.instruments]  
        self.tracks_by_instrument = self.get_track_by_instrument()
    
    # TODO: this function is deprecated <- remove from code
    def get_multiseq(self):
        '''tracks: list of SingleTrack objects
        reaturn a dictionary of sequences for every sequence in SingleTrack
        '''

        multiseq_indexes = set([key for music_track in self.tracks for key in music_track.seq])
        multiseq = dict()

        for seq_id in multiseq_indexes:
            multiseq[seq_id] = []

        for single_track in self.tracks:
            for key, value in single_track.seq.items():
                multiseq[key].append((single_track.name,value))

        return multiseq
    
    def get_pitch_offset_to_C(self):
        '''to get better train resoult without augmenting midis to all posible keys
        we assumed that most frequent note is the rootnote of song then calculate
        the offset of semitones to move song key to C.
        
        You should ADD this offset to note pitch to get it right
        '''
        
        hist = self.pm_obj.get_pitch_class_histogram()
        offset = np.argmax(hist)
        if offset > 6:
            return 12-offset
        else:
            return -offset
    
    def save(self, path):
        midi_file = pm.PrettyMIDI()
        for track in self.tracks:
            midi_file.instruments.append(track.to_pretty_midi_instrument(self.tempo))
        midi_file.write(path)
        return midi_file
    
    def get_track_by_instrument(self):
        '''return a dictionary with tracks indexes grouped by instrument class'''
        tracks = self.tracks
        names = [track.name for track in tracks]
        uniqe_instruemnts = set(names)
        tracks_by_instrument = dict()
        for key in uniqe_instruemnts:
            tracks_by_instrument[key] = []

        for i, track in enumerate(tracks):
            tracks_by_instrument[track.name].append(i)

        return tracks_by_instrument
    
    def get_common_bars_for_every_possible_pair(self, x_instrument, y_instrument):
        ''' for every possible pair of given instrument classes
        returns common bars from multitrack'''
        x_bars = []
        y_bars = []
        pairs = self.get_posible_pairs(x_instrument, y_instrument)
        for x_track_index, y_track_index in pairs:
            _x_bars, _y_bars = get_common_bars(self.tracks[x_track_index], self.tracks[y_track_index])
            x_bars.extend(_x_bars)
            y_bars.extend(_y_bars)

        return x_bars, y_bars
    
    def get_data_seq2seq_arrangment(self, x_instrument, y_instrument, bars_in_seq=4):
        '''this method is returning a sequances of given lenth by rolling this lists of x and y for arrangemt generation
        x and y has the same bar lenth, and represent the same musical phrase playd my difrent instruments (tracks) 
        
        '''
        x_seq = []
        y_seq = []
        x_bars, y_bars = self.get_common_bars_for_every_possible_pair(x_instrument, y_instrument)

        for i in range(len(x_bars) - bars_in_seq + 1):
            x_seq_to_add = [note for bar in x_bars[i:i+bars_in_seq] for note in bar ]
            y_seq_to_add = [note for bar in y_bars[i:i+bars_in_seq] for note in bar ]
            x_seq.append(x_seq_to_add)
            y_seq.append(y_seq_to_add)

        return x_seq, y_seq
    
    def get_data_seq2seq_melody(self,instrument_class, x_seq_len=4):
        '''return a list of bars with content for every track with given instrument class for melody generaiton
        x_seq_len and y_seq_len
        
        x previous sentence, y next sentence of the same melody line
        
        '''

        instrument_tracks = self.tracks_by_instrument[instrument_class]

        for track_index in instrument_tracks:
            bars = self.tracks[track_index].stream_to_bars()
            bars_indexes_with_content = get_bar_indexes_with_content(bars)
            bars_with_content = [bars[i] for i in get_bar_indexes_with_content(bars)]

            x_seq = []
            y_seq = []
            for i in range(len(bars_with_content)-x_seq_len-1):
                _x_seq = [note for bar in bars_with_content[i:i+x_seq_len] for note in bar]
                _y_bar = bars_with_content[i+x_seq_len]
                x_seq.append(_x_seq)
                y_seq.append(_y_bar)

        return x_seq, y_seq
    
    def get_posible_pairs(self, instrument_x, instrument_y):
        '''it takes two lists, and return a list of tuples with every posible 2-element combination
        parameters:
        -----------
            instrument_x, instrument_y : string {'Guitar','Bass','Drums'} 
                a string that represent a instrument class you want to look for in midi file.

        returns:
        ----------
            pairs: list of tuples
                a list of posible 2-element combination of two lists
        '''
        x_indexes = self.tracks_by_instrument[instrument_x]
        y_indexes = self.tracks_by_instrument[instrument_y]
        pairs = [(x,y) for x in x_indexes for y in y_indexes]
        return pairs
    
    def show_map(self):
        print(self.name)
        print()
        for track in self.tracks:
            bars = track.stream_to_bars(4)
            track_str = ''
            for bar in bars:
                if bar_has_content(bar):
                    track_str += '█'
                else:
                    track_str += '_'

            print(track.name[:4],':', track_str)
        

In [13]:
def extract_data(midi_folder_path=None, how=None, instrument=None, bar_in_seq=4, remove_duplicates=True):
    '''extract musical data from midis in given folder, to x_train, y_train lists on sequences
        
    parameters:
    -----------
        midi_folder_path : string 
            a path to directory where midi files are stored
        how : string {'melody','arrangment'}
            - if melody: function extract data of one instrument,
            and return lists of x and y that x is actual sequance of 4 bars
            and y is next bar
            - if arrangment: function extract data of two instruments and
            returns a lists of x and y that x is one instrument sequence,
            and y is coresponing sequance to x, played by second instrument
        instrument: string or tuple of two strings
            this parameter is used to specify a instrument class, or classes that you wanted
            to extract from midi files.
            
            if how='melody': string
            if how='arrangment' : (string_x, string_y)
            
    return:
    -------
        x_train, y_train - tuple of coresponding lists of x_train and y_train data for training set
        
    notes:
    ------
        extracted data is transposed to the key od C
        duplicated x,y pairs are removed
    '''
    if how not in {'melody','arrangment'}:
        raise ValueError('how parameter must by one of {melody,arrangment} ')

    x_train = []
    y_train = []

    for directory, subdirectories, files in os.walk(midi_folder_path):
        for midi_file in tqdm(files):
            midi_file_path = os.path.join(directory, midi_file)
            try:
                mt = MultiTrack(midi_file_path)
                if how=='melody':
                    x ,y = mt.get_data_seq2seq_melody(instrument, bar_in_seq)
                if how=='arrangment':
                    x ,y = mt.get_data_seq2seq_arrangment(instrument[0], instrument[1], bar_in_seq)
                x_train.extend(x)
                y_train.extend(y)
            except:
                continue
                
    if remove_duplicates:   
        x_train, y_train = remove_duplicated_sequences((x_train, y_train))
        
    return x_train , y_train

In [323]:
def stream_to_bars(notes, beat_per_bar=4):
        '''it takes notes and split it into equaly time distibuted sequances
        if note is between bars, the note is splited into two notes, with time sum equal to the note between bars.
        arguments:
            stream: list of "notes"
        return:
            bars: list: list of lists of notes, every list has equal time. in musical context it returns bars
        '''
        # TODO: if last bar of sequance has less notes to has time equal given bar lenth it is left shorter
        # fill the rest of bar with rests
        
        # FIXME: there is a problem, where note is longer that bar and negative time occured
        # split note to max_rest_note, the problem occured when note is longer then 2 bars
        
        bars = []
        time = 0
        bar_index = 0
        add_tail = False
        note_pitch = lambda note: note[0]
        note_len = lambda note: note[1]
        for note in notes:
            try:
                temp = bars[bar_index]
            except IndexError:
                bars.append([])
                
            if add_tail:
                tail_pitch = note_pitch(tail_note)
                while tail_note_len > beat_per_bar:
                    bars[bar_index].append((tail_pitch, beat_per_bar))
                    tail_note_len -= beat_per_bar
                    bar_index += 1
                       
                bars[bar_index].append((tail_pitch, tail_note_len))
                time += tail_note_len
                add_tail = False
            time += note_len(note)

            if time == beat_per_bar:
                bars[bar_index].append(note)
                time = 0
                bar_index += 1

            elif time > beat_per_bar: # if note is between bars
                between_bars_note_len =  note_len(note)
                tail_note_len = time - beat_per_bar
                leading_note_len = between_bars_note_len - tail_note_len
                leading_note = (note_pitch(note), leading_note_len)
                bars[bar_index].append(leading_note)
                tail_note = (note_pitch(note), tail_note_len)

                add_tail = True
                time = 0
                bar_index += 1
            else:
                bars[bar_index].append(note)
                
        return bars

In [31]:
# def main():
#     '''extract data from midis
#     '''
    
# #     midi_folder_path = sys.argv[0]
# #     how = sys.argv[1]
# #     instrument = tuple(sys.argv[2].split('>')) if how == 'arrangment' else sys.argv[2]
# #     bar_in_seq = int(sys.argv[3])
# #     dataset_output_path = sys.argv[4]
    
#     x_train, y_train = extract_data(midi_folder_path='The Offspring', how='melody', 
#                                     instrument='Guitar', bar_in_seq=4)
#     pickle.dump((x_train, y_train), open('offspring_guitar_data.pkl','wb'))
#     return x_train, y_train

In [32]:
# if __name__=='__main__':
#     x_train, y_train = main()

100%|██████████| 28/28 [00:06<00:00,  4.06it/s]


# model.py

## encoder

In [15]:
class Seq2SeqTransformer():
    ''' encoder/transforer 
    params:
    -------
        x_train, y_train - list of sequences

    methods:
        fit
        transform'''
    
    def __init__(self):
        self.transform_dict = None
        self.reverse_dict = None
        self.vocab_x = None
        self.vocab_y = None
        
        
    def preprocess(self, x_train, y_train):
        _x_train = []
        for i, seq in enumerate(x_train):
            _x_train.append([])
            for note in seq:
                _x_train[i].append(note)

        _y_train = []
        for i, seq in enumerate(y_train):
            _y_train.append([])
            _y_train[i].append('<GO>')
            for note in seq:
                    _y_train[i].append(note)
            _y_train[i].append('<EOS>')
                    
        return _x_train, _y_train

    def transform(self, x_train, y_train):
        
        x_vocab = set([note for seq in x_train for note in seq])
        y_vocab = set([note for seq in y_train for note in seq])
        
        self.x_vocab = sorted(list(x_vocab)) 
        self.y_vocab = ['<GO>','<EOS>']
        self.y_vocab.extend(sorted(list(y_vocab)))

        self.x_vocab_size = len(self.x_vocab)
        self.y_vocab_size = len(self.y_vocab)


        self.x_transform_dict = dict(
            [(char, i) for i, char in enumerate(self.x_vocab)])
        self.y_transform_dict = dict(
            [(char, i) for i, char in enumerate(self.y_vocab)])
        self.x_reverse_dict = dict(
            (i, char) for char, i in self.x_transform_dict.items())
        self.y_reverse_dict = dict(
            (i, char) for char, i in self.y_transform_dict.items())
        
#     def transform(self, _x_train, _y_train):
        
        x_train, y_train = self.preprocess(x_train, y_train)
        
        self.x_max_seq_length = max([len(seq) for seq in x_train])
        self.y_max_seq_length = max([len(seq) for seq in y_train])
        
        encoder_input_data = np.zeros(
            (len(x_train), self.x_max_seq_length, self.x_vocab_size),
            dtype='float32')
        decoder_input_data = np.zeros(
            (len(x_train), self.y_max_seq_length, self.y_vocab_size),
            dtype='float32')
        decoder_target_data = np.zeros(
            (len(x_train), self.y_max_seq_length, self.y_vocab_size),
            dtype='float32')

        for i, (x_train, y_train) in enumerate(zip(x_train, y_train)):
            for t, char in enumerate(x_train):
                encoder_input_data[i, t,  self.x_transform_dict[char]] = 1.
            for t, char in enumerate(y_train):
                decoder_input_data[i, t,  self.y_transform_dict[char]] = 1.
                if t > 0:
                    decoder_target_data[i, t - 1,  self.y_transform_dict[char]] = 1.
                    
        return encoder_input_data, decoder_input_data, decoder_target_data # return seq2seq _data object?

In [38]:
from __future__ import print_function

from keras.models import Model, load_model
from keras.layers import Input, LSTM, Dense
import numpy as np

In [549]:
class Seq2SeqModel():
    '''NeuralNerwork Seq2Seq model.
    The network is created based on training data
    '''

    def __init__(self, latent_dim, x_train, y_train):
        self.has_predict_model = False
        self.has_train_model = False
        self.x_train = x_train
        self.y_train = y_train
        self.latent_dim = latent_dim
        self.transformer = Seq2SeqTransformer()
        self.encoder_input_data, self.decoder_input_data, self.decoder_target_data = self.transformer.transform(self.x_train, self.y_train)
    
        # ---------------
        # SEQ 2 SEQ MODEL:
        #     INPUT_1 : encoder_input_data
        #     INPUT_2 : decodet_input_data
        #     OUTPUT : decoder_target_data
        # ---------------
        
        # ENCODER MODEL
        #---------------
        
        # 1 layer - Input : encoder_input_data
        self.encoder_inputs = Input(shape=(None, self.transformer.x_vocab_size ))
        
        # 2 layer - LSTM_1
        self.encoder = LSTM(latent_dim, return_state=True)
        
        # 2 layer - LSTM_1 : outputs
        self.encoder_outputs, self.state_h, self.state_c = self.encoder(self.encoder_inputs)
        self.encoder_states = [self.state_h, self.state_c]  
        
       
        # DECODER MODEL
        #---------------
        
        # 1 layer - Input : decoder_input_data
        self.decoder_inputs = Input(shape=(None, self.transformer.y_vocab_size)) 
        
        # 2 layer - LSTM_1
        self.decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
        
        # 2 layer - LSTM_2 : outputs, full sequance as lstm layer
        self.decoder_outputs, _, _ = self.decoder_lstm(self.decoder_inputs,                     
                                                  initial_state=self.encoder_states)
        
        # 3 layer - Dense
        self.decoder_dense = Dense(self.transformer.y_vocab_size, activation='softmax')
        
        # 3 layer - Dense : outputs, full sequance as the array of one-hot-encoded elements 
        self.decoder_outputs = self.decoder_dense(self.decoder_outputs)
        
    def init_train_model(self):
        self.train_model = Model([self.encoder_inputs, self.decoder_inputs], self.decoder_outputs)
        self.train_model.compile(optimizer='rmsprop', loss='categorical_crossentropy')
        
    def fit(self, batch_size, epochs):     
        
        if not self.has_train_model:
            self.init_train_model()
            self.has_train_model = True
        
        
        self.train_model.fit([self.encoder_input_data, self.decoder_input_data], self.decoder_target_data,
                              batch_size=batch_size,
                              epochs=epochs,
                              validation_split=0.2)
    def save(self, path):
        self.train_model.save(path)
    
    def load(self, path):
        self.train_model = load_model(path)
        self.has_train_model = True
        
        self.encoder_inputs = self.train_model.layers[0].input
        self.encoder = self.train_model.layers[2]
        self.encoder_outputs, self.state_h, self.state_c = self.train_model.layers[2].output
        self.encoder_states = [self.state_h, self.state_c]  
        self.decoder_inputs = self.train_model.layers[1].input
        self.decoder_lstm = self.train_model.layers[3]
        self.decoder_outputs, _, _ = self.train_model.layers[3].output
        self.decoder_dense = self.train_model.layers[4]
        self.decoder_outputs = self.train_model.layers[4].output
            
    def init_predict_model(self):
        
        # ENCODER MODEL <- note used in develop music process
        #     from encoder_input to encoder_states
        #     to give a context to decoder model
        #---------------------------------
        
        self.encoder_model = Model(self.encoder_inputs, self.encoder_states)

        
        # DECODER MODEL
        #     From states (context) to sequance by generating firts element from context vector
        #     and starting element <GO>. Then adding predicted element as input to next cell, with
        #     updated states (context) by prevously generated element.
        #   
        #     INPUT_1 : state_h
        #     INPUT_2 : state_c
        #     INPUT_3 : y_train sized layer, that will be recursivly generated starting from <GO> sign
        #     
        #     INPUT -> LSTM -> DENSE
        #
        #     OUTPUT : one-hot-encoded element of sequance
        #     OUTPUT : state_h (updated)
        #     OUTPUT : state_c (updated)
        # -------------
        
        # 1 layer: TWO INPUTS: decoder_state_h, decoder_state_c
        self.decoder_state_input_h = Input(shape=(latent_dim,))  
        self.decoder_state_input_c = Input(shape=(latent_dim,))
        self.decoder_states_inputs = [self.decoder_state_input_h, self.decoder_state_input_c]
        
        # 2 layer: LSTM_1 output: element of sequance, lstm cell states
        self.decoder_outputs, self.state_h, self.state_c = self.decoder_lstm(
            self.decoder_inputs, initial_state = self.decoder_states_inputs)
        self.decoder_states = [self.state_h, self.state_c]
        
        # 3 layer: Dense output: one-hot-encoded representation of element of sequance
        self.decoder_outputs = self.decoder_dense(self.decoder_outputs)

        
        self.decoder_model = Model(                               
            [self.decoder_inputs] + self.decoder_states_inputs,
            [self.decoder_outputs] + self.decoder_states)
        self.has_predict_model = True
        
    def predict(self, input_seq=None, mode=None):
        
        if not self.has_predict_model:
            self.init_predict_model()
            self.has_predict_model = True
        
        if mode == 'generate':
            # create a random context as starting point
            h = np.random.rand(1,self.latent_dim)*2 - 1
            c = np.random.rand(1,self.latent_dim)*2 - 1
            states_value = [h, c]
        else:
            # get context from input sequance
            states_value = self.encoder_model.predict(input_seq)

        # make the empty decoder_input_data
        # and create the starting <GO> element of decoder_input_data
        target_seq = np.zeros((1, 1, self.transformer.y_vocab_size))  
        target_seq[0, 0, self.transformer.y_transform_dict['<GO>']] = 1.

        # sequance generation loop of decoder model
        stop_condition = False
        decoded_sentence = []
#         time = 0
        while not stop_condition:            
            
            # INPUT_1 : target_seq : started from empty array with start <GO> char
            # and recursivly updated by predicted elements
            
            # INPUT_2 : states_value :context from encoder model or randomly generated in develop mode
            # this can give as a 2 * latent_dim parameters to play with in manual generation
            
            # OUTPUT_1 : output_tokens : one hot encoded predicted element of sequance
            # OUTPUT_2,3 : h, c : context updated by predicted element
            output_tokens, h, c = self.decoder_model.predict(
                [target_seq] + states_value)

            # get most likly element index
            # translate from index to final (in normal form) preidcted element
            # append it to output list
            sampled_token_index = np.argmax(output_tokens[0, -1, :])
            sampled_char = self.transformer.y_reverse_dict[sampled_token_index]
            decoded_sentence.append(sampled_char)
            
#             time += sampled_char[1]
            # or time>=16
            if (sampled_char == '<EOS>' or len(decoded_sentence) > self.transformer.y_max_seq_length ):
                stop_condition = True

            target_seq = np.zeros((1, 1, self.transformer.y_vocab_size))
            target_seq[0, 0, sampled_token_index] = 1.

            states_value = [h, c]

        return decoded_sentence
    
    def develop(self, mode='from_seq'):
        
        # music generation for seq2seq for melody
        input_seq_start = random_seed_generator(16,
                                                self.transformer.x_max_seq_length,
                                                self.transformer.x_vocab_size,
                                                self.transformer.x_transform_dict,
                                                self.transformer.x_reverse_dict)
        
        input_data = seq_to_numpy(input_seq_start,
                                  self.transformer.x_max_seq_length,
                                  self.transformer.x_vocab_size,
                                  self.transformer.x_transform_dict)

        # generate sequnce iterativly for melody
        input_seq = input_seq_start.copy()
        melody = []
        for i in range(4):
            if mode == 'from_seq':
                decoded_sentence = self.predict(input_data)[:-1]
            elif mode == 'from_state':
                decoded_sentence = self.predict(mode='generate')[:-1]
            else:
                raise ValueError('mode must be in {from_seq, from_state}')
            melody.append(decoded_sentence)
            input_seq.extend(decoded_sentence)
            input_bars = stream_to_bars(input_seq)
            input_bars = input_bars[1:5]
            input_seq = [note for bar in input_bars for note in bar]
            input_data = seq_to_numpy(input_seq,
                                      self.transformer.x_max_seq_length,
                                      self.transformer.x_vocab_size,
                                      self.transformer.x_transform_dict)

        melody = [note for bar in melody for note in bar]
        return melody

In [499]:
def random_seed_generator(time_of_seq, max_encoder_seq_length, num_encoder_tokens, input_token_index, reverse_input_char_index):
    time = 0
    random_seq = []
    items = 0
    stop_sign = False
    while (time < time_of_seq):
        seed = randint(0,num_encoder_tokens-1)
        note = reverse_input_char_index[seed]
        time += note[1]
        if time > time_of_seq:
            note_time = note[1] - (time-time_of_seq)
            trimmed_note = (note[0],note_time)
            try:
                seed = input_token_index[trimmed_note]
                random_seq.append(trimmed_note)
                items += 1
            except KeyError:
                time -= note[1]
                continue
        else:
            random_seq.append(note)
            items += 1
        
        if items > max_encoder_seq_length:
            time = 0
            random_seq = []
            items = 0
            stop_sign = False
            
        
    return random_seq  

In [501]:
# seq to numpy array:
def seq_to_numpy(seq, max_encoder_seq_length, num_encoder_tokens, input_token_index):
    input_data = np.zeros(
        (1, max_encoder_seq_length, num_encoder_tokens),
        dtype='float32')

    for t, char in enumerate(seq):
        try:
            input_data[0, t, input_token_index[char]] = 1.
        except KeyError:
            char_time = char[1]
            _char = ((-1,), char_time)
        except IndexError:
            break

    return input_data

# train.py

## data extraction

In [21]:
midi_folder_path = 'midi_pack'

In [25]:
# Guitar
guitar_x_train, guitar_y_train = extract_data(midi_folder_path=midi_folder_path, how='melody', 
                                              instrument='Guitar', bar_in_seq=4)

pickle.dump((guitar_x_train, guitar_y_train), open('training_set/offspring_guitar_data.pkl','wb'))

100%|██████████| 28/28 [00:06<00:00,  4.02it/s]


In [26]:
melody_x_train, melody_y_train = extract_data(midi_folder_path=midi_folder_path, how='arrangment', 
                                              instrument=('Guitar', 'Melody'), bar_in_seq=4)
pickle.dump((melody_x_train, melody_y_train), open('training_set/offspring_melody_data.pkl','wb'))

100%|██████████| 28/28 [00:08<00:00,  1.51it/s]


In [27]:
bass_x_train, bass_y_train = extract_data(midi_folder_path=midi_folder_path, how='arrangment', 
                                          instrument=('Guitar', 'Bass'), bar_in_seq=4)

pickle.dump((bass_x_train, bass_y_train), open('training_set/offspring_bass_data.pkl','wb'))

100%|██████████| 28/28 [00:06<00:00,  4.20it/s]


In [28]:
drums_x_train, drums_y_train = extract_data(midi_folder_path=midi_folder_path, how='arrangment', 
                                            instrument=('Bass', 'Drums'), bar_in_seq=4)

pickle.dump((drums_x_train, drums_y_train), open('training_set/offspring_drums_data.pkl','wb'))

100%|██████████| 28/28 [00:06<00:00,  4.36it/s]


## model training

In [29]:
# settings for training
batch_size = 64  
epochs = 4
latent_dim = 256
num_samples = 10000 

In [45]:
'''GUITAR'''
# make model, and train from zero
guitar_x_train, guitar_y_train = pickle.load(open('training_set/offspring_guitar_data.pkl','rb'))
guitar_model = Seq2SeqModel(latent_dim, guitar_x_train, guitar_y_train)
guitar_model.fit(batch_size, 500)
guitar_model.save('models/offspring_guitar_model.h5')

Train on 789 samples, validate on 198 samples
Epoch 1/1
789/789 [==============================] - ETA: 30s - loss: 2.74 - ETA: 15s - loss: 2.71 - ETA: 10s - loss: 2.82 - ETA: 7s - loss: 2.7931 - ETA: 5s - loss: 2.707 - ETA: 4s - loss: 2.630 - ETA: 3s - loss: 2.570 - ETA: 2s - loss: 2.521 - ETA: 1s - loss: 2.488 - ETA: 1s - loss: 2.445 - ETA: 0s - loss: 2.423 - ETA: 0s - loss: 2.395 - 7s 9ms/step - loss: 2.3926 - val_loss: 1.9593


c:\software\python3\lib\site-packages\keras\engine\network.py:877: UserWarning: Layer lstm_24 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_23/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_23/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


In [ ]:
# load saved model and train more
guitar_x_train, guitar_y_train = pickle.load(open('training_set/offspring_guitar_data.pkl','rb'))
guitar_model = Seq2SeqModel(latent_dim, guitar_x_train, guitar_y_train)
guitar_model.load('models/offspring_guitar_model.h5')
guitar_model.fit(batch_size, 500)
guitar_model.save('models/offspring_guitar_model.h5')

In [51]:
'''MELODY'''
# make model, and train from zero
melody_x_train, melody_y_train = pickle.load(open('training_set/offspring_melody_data.pkl','rb'))
melody_model = Seq2SeqModel(latent_dim, melody_x_train, melody_y_train)
melody_model.fit(batch_size, 500)
melody_model.save('models/offspring_melody_model.h5')

Train on 1902 samples, validate on 476 samples
Epoch 1/500
1902/1902 [==============================] - ETA: 1:59 - loss: 1.981 - ETA: 1:07 - loss: 1.934 - ETA: 49s - loss: 1.955 - ETA: 40s - loss: 1.86 - ETA: 34s - loss: 1.82 - ETA: 30s - loss: 1.76 - ETA: 27s - loss: 1.74 - ETA: 24s - loss: 1.70 - ETA: 22s - loss: 1.68 - ETA: 20s - loss: 1.66 - ETA: 19s - loss: 1.64 - ETA: 17s - loss: 1.63 - ETA: 16s - loss: 1.62 - ETA: 15s - loss: 1.60 - ETA: 13s - loss: 1.59 - ETA: 12s - loss: 1.58 - ETA: 11s - loss: 1.58 - ETA: 10s - loss: 1.57 - ETA: 9s - loss: 1.5614 - ETA: 8s - loss: 1.561 - ETA: 7s - loss: 1.558 - ETA: 6s - loss: 1.552 - ETA: 5s - loss: 1.549 - ETA: 4s - loss: 1.545 - ETA: 4s - loss: 1.547 - ETA: 3s - loss: 1.543 - ETA: 2s - loss: 1.542 - ETA: 1s - loss: 1.538 - ETA: 0s - loss: 1.536 - 28s 15ms/step - loss: 1.5384 - val_loss: 1.5017
Epoch 2/500
1902/1902 [==============================] - ETA: 20s - loss: 1.53 - ETA: 19s - loss: 1.54 - ETA: 18s - loss: 1.53 - ETA: 18s - loss: 

1902/1902 [==============================] - ETA: 22s - loss: 0.94 - ETA: 21s - loss: 0.96 - ETA: 20s - loss: 0.94 - ETA: 19s - loss: 0.94 - ETA: 18s - loss: 0.94 - ETA: 18s - loss: 0.94 - ETA: 17s - loss: 0.93 - ETA: 16s - loss: 0.93 - ETA: 15s - loss: 0.93 - ETA: 15s - loss: 0.93 - ETA: 14s - loss: 0.94 - ETA: 13s - loss: 0.93 - ETA: 12s - loss: 0.93 - ETA: 12s - loss: 0.93 - ETA: 11s - loss: 0.94 - ETA: 10s - loss: 0.93 - ETA: 9s - loss: 0.9336 - ETA: 8s - loss: 0.935 - ETA: 8s - loss: 0.935 - ETA: 7s - loss: 0.934 - ETA: 6s - loss: 0.934 - ETA: 5s - loss: 0.931 - ETA: 5s - loss: 0.929 - ETA: 4s - loss: 0.931 - ETA: 3s - loss: 0.928 - ETA: 2s - loss: 0.925 - ETA: 2s - loss: 0.928 - ETA: 1s - loss: 0.927 - ETA: 0s - loss: 0.926 - 26s 14ms/step - loss: 0.9249 - val_loss: 0.9098
Epoch 12/500
1902/1902 [==============================] - ETA: 21s - loss: 0.89 - ETA: 21s - loss: 0.90 - ETA: 20s - loss: 0.88 - ETA: 20s - loss: 0.89 - ETA: 19s - loss: 0.88 - ETA: 18s - loss: 0.87 - ETA: 18s

1902/1902 [==============================] - ETA: 22s - loss: 0.57 - ETA: 21s - loss: 0.57 - ETA: 20s - loss: 0.58 - ETA: 20s - loss: 0.58 - ETA: 19s - loss: 0.59 - ETA: 18s - loss: 0.59 - ETA: 17s - loss: 0.58 - ETA: 17s - loss: 0.58 - ETA: 16s - loss: 0.59 - ETA: 15s - loss: 0.58 - ETA: 14s - loss: 0.58 - ETA: 13s - loss: 0.58 - ETA: 13s - loss: 0.58 - ETA: 12s - loss: 0.58 - ETA: 11s - loss: 0.58 - ETA: 10s - loss: 0.58 - ETA: 9s - loss: 0.5835 - ETA: 9s - loss: 0.584 - ETA: 8s - loss: 0.582 - ETA: 7s - loss: 0.582 - ETA: 6s - loss: 0.580 - ETA: 6s - loss: 0.578 - ETA: 5s - loss: 0.579 - ETA: 4s - loss: 0.579 - ETA: 3s - loss: 0.578 - ETA: 2s - loss: 0.578 - ETA: 2s - loss: 0.578 - ETA: 1s - loss: 0.578 - ETA: 0s - loss: 0.577 - 26s 14ms/step - loss: 0.5781 - val_loss: 0.6146
Epoch 22/500
1902/1902 [==============================] - ETA: 23s - loss: 0.58 - ETA: 23s - loss: 0.56 - ETA: 22s - loss: 0.55 - ETA: 21s - loss: 0.55 - ETA: 20s - loss: 0.55 - ETA: 19s - loss: 0.56 - ETA: 18s

1902/1902 [==============================] - ETA: 22s - loss: 0.38 - ETA: 21s - loss: 0.38 - ETA: 20s - loss: 0.37 - ETA: 19s - loss: 0.37 - ETA: 19s - loss: 0.38 - ETA: 18s - loss: 0.38 - ETA: 17s - loss: 0.38 - ETA: 16s - loss: 0.37 - ETA: 16s - loss: 0.38 - ETA: 15s - loss: 0.38 - ETA: 14s - loss: 0.37 - ETA: 13s - loss: 0.37 - ETA: 12s - loss: 0.37 - ETA: 12s - loss: 0.37 - ETA: 11s - loss: 0.37 - ETA: 10s - loss: 0.37 - ETA: 9s - loss: 0.3701 - ETA: 9s - loss: 0.370 - ETA: 8s - loss: 0.371 - ETA: 7s - loss: 0.371 - ETA: 6s - loss: 0.372 - ETA: 5s - loss: 0.373 - ETA: 5s - loss: 0.373 - ETA: 4s - loss: 0.372 - ETA: 3s - loss: 0.372 - ETA: 2s - loss: 0.371 - ETA: 2s - loss: 0.371 - ETA: 1s - loss: 0.371 - ETA: 0s - loss: 0.370 - 26s 14ms/step - loss: 0.3691 - val_loss: 0.4309
Epoch 32/500
1902/1902 [==============================] - ETA: 23s - loss: 0.34 - ETA: 22s - loss: 0.34 - ETA: 21s - loss: 0.34 - ETA: 20s - loss: 0.34 - ETA: 19s - loss: 0.34 - ETA: 19s - loss: 0.34 - ETA: 18s

1902/1902 [==============================] - ETA: 22s - loss: 0.23 - ETA: 21s - loss: 0.24 - ETA: 21s - loss: 0.25 - ETA: 20s - loss: 0.25 - ETA: 19s - loss: 0.25 - ETA: 18s - loss: 0.25 - ETA: 17s - loss: 0.24 - ETA: 17s - loss: 0.24 - ETA: 16s - loss: 0.24 - ETA: 15s - loss: 0.24 - ETA: 14s - loss: 0.24 - ETA: 13s - loss: 0.24 - ETA: 13s - loss: 0.24 - ETA: 12s - loss: 0.24 - ETA: 11s - loss: 0.24 - ETA: 10s - loss: 0.24 - ETA: 10s - loss: 0.24 - ETA: 9s - loss: 0.2463 - ETA: 8s - loss: 0.245 - ETA: 7s - loss: 0.244 - ETA: 6s - loss: 0.244 - ETA: 6s - loss: 0.245 - ETA: 5s - loss: 0.246 - ETA: 4s - loss: 0.246 - ETA: 3s - loss: 0.246 - ETA: 2s - loss: 0.245 - ETA: 2s - loss: 0.245 - ETA: 1s - loss: 0.246 - ETA: 0s - loss: 0.247 - 26s 14ms/step - loss: 0.2473 - val_loss: 0.3482
Epoch 42/500
1902/1902 [==============================] - ETA: 23s - loss: 0.24 - ETA: 22s - loss: 0.23 - ETA: 21s - loss: 0.24 - ETA: 20s - loss: 0.24 - ETA: 19s - loss: 0.23 - ETA: 18s - loss: 0.24 - ETA: 18s

...

1902/1902 [==============================] - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 15s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0128 - ETA: 8s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 3s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 1s - loss: 0.013 - ETA: 0s - loss: 0.013 - 26s 14ms/step - loss: 0.0139 - val_loss: 0.2419
Epoch 462/500
1902/1902 [==============================] - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17

1902/1902 [==============================] - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 15s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0140 - ETA: 9s - loss: 0.014 - ETA: 8s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.014 - ETA: 6s - loss: 0.014 - ETA: 5s - loss: 0.014 - ETA: 4s - loss: 0.014 - ETA: 3s - loss: 0.014 - ETA: 2s - loss: 0.014 - ETA: 2s - loss: 0.014 - ETA: 1s - loss: 0.014 - ETA: 0s - loss: 0.014 - 26s 14ms/step - loss: 0.0144 - val_loss: 0.2420
Epoch 472/500
1902/1902 [==============================] - ETA: 23s - loss: 0.01 - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17

1902/1902 [==============================] - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17s - loss: 0.01 - ETA: 17s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 15s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0132 - ETA: 9s - loss: 0.013 - ETA: 8s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 3s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 1s - loss: 0.013 - ETA: 0s - loss: 0.013 - 26s 14ms/step - loss: 0.0137 - val_loss: 0.2428
Epoch 482/500
1902/1902 [==============================] - ETA: 21s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17

1902/1902 [==============================] - ETA: 23s - loss: 0.00 - ETA: 21s - loss: 0.00 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 16s - loss: 0.01 - ETA: 15s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0130 - ETA: 9s - loss: 0.013 - ETA: 8s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 3s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 1s - loss: 0.013 - ETA: 0s - loss: 0.013 - 26s 14ms/step - loss: 0.0134 - val_loss: 0.2434
Epoch 492/500
1902/1902 [==============================] - ETA: 22s - loss: 0.01 - ETA: 21s - loss: 0.01 - ETA: 20s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 19s - loss: 0.01 - ETA: 18s - loss: 0.01 - ETA: 17

c:\software\python3\lib\site-packages\keras\engine\network.py:877: UserWarning: Layer lstm_36 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_35/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_35/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


In [ ]:
# load saved model and train more
melody_x_train, melody_y_train = pickle.load(open('training_set/offspring_melody_data.pkl','rb'))
guitar_model = Seq2SeqModel(latent_dim, melody_x_train, melody_y_train)
melody_model.load('models/offspring_melody_model.h5')
melody_model.fit(batch_size, 500)
melody_model.save('models/offspring_melody_model.h5')

In [52]:
'''BASS'''
# make model, and train from zero
bass_x_train, bass_y_train = pickle.load(open('training_set/offspring_bass_data.pkl','rb'))
bass_model = Seq2SeqModel(latent_dim, bass_x_train, bass_y_train)
bass_model.fit(batch_size, 500)
bass_model.save('models/offspring_bass_model.h5')

Train on 1407 samples, validate on 352 samples
Epoch 1/500
1407/1407 [==============================] - ETA: 1:38 - loss: 2.086 - ETA: 53s - loss: 2.157 - ETA: 38s - loss: 2.15 - ETA: 30s - loss: 2.10 - ETA: 25s - loss: 2.07 - ETA: 21s - loss: 2.02 - ETA: 18s - loss: 1.99 - ETA: 16s - loss: 1.95 - ETA: 14s - loss: 1.91 - ETA: 13s - loss: 1.87 - ETA: 11s - loss: 1.84 - ETA: 10s - loss: 1.82 - ETA: 9s - loss: 1.8052 - ETA: 7s - loss: 1.791 - ETA: 6s - loss: 1.771 - ETA: 5s - loss: 1.760 - ETA: 4s - loss: 1.743 - ETA: 3s - loss: 1.737 - ETA: 2s - loss: 1.719 - ETA: 1s - loss: 1.708 - ETA: 0s - loss: 1.699 - 22s 15ms/step - loss: 1.6967 - val_loss: 1.5690
Epoch 2/500
1407/1407 [==============================] - ETA: 14s - loss: 1.47 - ETA: 13s - loss: 1.48 - ETA: 12s - loss: 1.50 - ETA: 11s - loss: 1.49 - ETA: 11s - loss: 1.49 - ETA: 10s - loss: 1.49 - ETA: 9s - loss: 1.4875 - ETA: 9s - loss: 1.469 - ETA: 8s - loss: 1.474 - ETA: 8s - loss: 1.480 - ETA: 7s - loss: 1.481 - ETA: 6s - loss: 1.

1407/1407 [==============================] - ETA: 14s - loss: 0.69 - ETA: 13s - loss: 0.66 - ETA: 13s - loss: 0.65 - ETA: 12s - loss: 0.64 - ETA: 11s - loss: 0.64 - ETA: 11s - loss: 0.64 - ETA: 10s - loss: 0.63 - ETA: 9s - loss: 0.6361 - ETA: 9s - loss: 0.633 - ETA: 8s - loss: 0.634 - ETA: 7s - loss: 0.632 - ETA: 6s - loss: 0.631 - ETA: 6s - loss: 0.628 - ETA: 5s - loss: 0.631 - ETA: 4s - loss: 0.629 - ETA: 4s - loss: 0.629 - ETA: 3s - loss: 0.636 - ETA: 2s - loss: 0.638 - ETA: 2s - loss: 0.638 - ETA: 1s - loss: 0.636 - ETA: 0s - loss: 0.636 - 17s 12ms/step - loss: 0.6333 - val_loss: 0.6384
Epoch 15/500
1407/1407 [==============================] - ETA: 14s - loss: 0.57 - ETA: 13s - loss: 0.59 - ETA: 13s - loss: 0.59 - ETA: 12s - loss: 0.58 - ETA: 11s - loss: 0.59 - ETA: 11s - loss: 0.58 - ETA: 10s - loss: 0.58 - ETA: 9s - loss: 0.5807 - ETA: 9s - loss: 0.581 - ETA: 8s - loss: 0.596 - ETA: 7s - loss: 0.598 - ETA: 6s - loss: 0.599 - ETA: 6s - loss: 0.594 - ETA: 5s - loss: 0.596 - ETA: 4s

1407/1407 [==============================] - ETA: 14s - loss: 0.37 - ETA: 13s - loss: 0.37 - ETA: 13s - loss: 0.35 - ETA: 12s - loss: 0.34 - ETA: 11s - loss: 0.34 - ETA: 11s - loss: 0.34 - ETA: 10s - loss: 0.34 - ETA: 9s - loss: 0.3444 - ETA: 9s - loss: 0.341 - ETA: 8s - loss: 0.339 - ETA: 7s - loss: 0.343 - ETA: 7s - loss: 0.342 - ETA: 6s - loss: 0.345 - ETA: 5s - loss: 0.347 - ETA: 4s - loss: 0.349 - ETA: 4s - loss: 0.352 - ETA: 3s - loss: 0.354 - ETA: 2s - loss: 0.354 - ETA: 2s - loss: 0.352 - ETA: 1s - loss: 0.352 - ETA: 0s - loss: 0.351 - 17s 12ms/step - loss: 0.3521 - val_loss: 0.3861
Epoch 28/500
1407/1407 [==============================] - ETA: 14s - loss: 0.34 - ETA: 14s - loss: 0.32 - ETA: 13s - loss: 0.34 - ETA: 13s - loss: 0.34 - ETA: 12s - loss: 0.33 - ETA: 11s - loss: 0.33 - ETA: 10s - loss: 0.34 - ETA: 10s - loss: 0.34 - ETA: 9s - loss: 0.3392 - ETA: 8s - loss: 0.341 - ETA: 7s - loss: 0.343 - ETA: 7s - loss: 0.340 - ETA: 6s - loss: 0.341 - ETA: 5s - loss: 0.342 - ETA: 5s

1407/1407 [==============================] - ETA: 14s - loss: 0.20 - ETA: 13s - loss: 0.22 - ETA: 13s - loss: 0.23 - ETA: 12s - loss: 0.24 - ETA: 11s - loss: 0.23 - ETA: 11s - loss: 0.23 - ETA: 10s - loss: 0.23 - ETA: 9s - loss: 0.2312 - ETA: 9s - loss: 0.228 - ETA: 8s - loss: 0.228 - ETA: 7s - loss: 0.228 - ETA: 6s - loss: 0.228 - ETA: 6s - loss: 0.230 - ETA: 5s - loss: 0.232 - ETA: 4s - loss: 0.231 - ETA: 4s - loss: 0.231 - ETA: 3s - loss: 0.232 - ETA: 2s - loss: 0.230 - ETA: 2s - loss: 0.229 - ETA: 1s - loss: 0.229 - ETA: 0s - loss: 0.230 - 17s 12ms/step - loss: 0.2300 - val_loss: 0.2868
Epoch 41/500
1407/1407 [==============================] - ETA: 14s - loss: 0.22 - ETA: 14s - loss: 0.22 - ETA: 13s - loss: 0.22 - ETA: 12s - loss: 0.22 - ETA: 11s - loss: 0.23 - ETA: 11s - loss: 0.23 - ETA: 10s - loss: 0.22 - ETA: 9s - loss: 0.2289 - ETA: 8s - loss: 0.226 - ETA: 8s - loss: 0.225 - ETA: 7s - loss: 0.223 - ETA: 6s - loss: 0.222 - ETA: 6s - loss: 0.221 - ETA: 5s - loss: 0.221 - ETA: 4s

1407/1407 [==============================] - ETA: 14s - loss: 0.14 - ETA: 13s - loss: 0.14 - ETA: 13s - loss: 0.14 - ETA: 12s - loss: 0.14 - ETA: 11s - loss: 0.14 - ETA: 11s - loss: 0.15 - ETA: 10s - loss: 0.15 - ETA: 9s - loss: 0.1614 - ETA: 8s - loss: 0.161 - ETA: 8s - loss: 0.163 - ETA: 7s - loss: 0.161 - ETA: 6s - loss: 0.162 - ETA: 6s - loss: 0.161 - ETA: 5s - loss: 0.160 - ETA: 4s - loss: 0.159 - ETA: 4s - loss: 0.159 - ETA: 3s - loss: 0.160 - ETA: 2s - loss: 0.161 - ETA: 2s - loss: 0.162 - ETA: 1s - loss: 0.163 - ETA: 0s - loss: 0.164 - 17s 12ms/step - loss: 0.1647 - val_loss: 0.2205
Epoch 54/500
1407/1407 [==============================] - ETA: 14s - loss: 0.15 - ETA: 13s - loss: 0.15 - ETA: 12s - loss: 0.14 - ETA: 12s - loss: 0.15 - ETA: 11s - loss: 0.15 - ETA: 11s - loss: 0.15 - ETA: 10s - loss: 0.15 - ETA: 9s - loss: 0.1621 - ETA: 8s - loss: 0.164 - ETA: 8s - loss: 0.166 - ETA: 7s - loss: 0.166 - ETA: 6s - loss: 0.166 - ETA: 6s - loss: 0.166 - ETA: 5s - loss: 0.164 - ETA: 4s

...

1407/1407 [==============================] - ETA: 14s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0126 - ETA: 8s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 3s - loss: 0.012 - ETA: 2s - loss: 0.013 - ETA: 2s - loss: 0.013 - ETA: 1s - loss: 0.013 - ETA: 0s - loss: 0.013 - 17s 12ms/step - loss: 0.0132 - val_loss: 0.1758
Epoch 457/500
1407/1407 [==============================] - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0112 - ETA: 8s - loss: 0.011 - ETA: 8s - loss: 0.011 - ETA: 7s - loss: 0.012 - ETA: 6s - loss: 0.013 - ETA: 6s - loss: 0.015 - ETA: 5s - loss: 0.016 - ETA: 4

1407/1407 [==============================] - ETA: 14s - loss: 0.02 - ETA: 13s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0143 - ETA: 8s - loss: 0.014 - ETA: 8s - loss: 0.014 - ETA: 7s - loss: 0.014 - ETA: 6s - loss: 0.013 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4s - loss: 0.013 - ETA: 4s - loss: 0.014 - ETA: 3s - loss: 0.015 - ETA: 2s - loss: 0.015 - ETA: 2s - loss: 0.015 - ETA: 1s - loss: 0.015 - ETA: 0s - loss: 0.014 - 17s 12ms/step - loss: 0.0146 - val_loss: 0.1854
Epoch 470/500
1407/1407 [==============================] - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.00 - ETA: 12s - loss: 0.00 - ETA: 11s - loss: 0.00 - ETA: 10s - loss: 0.00 - ETA: 10s - loss: 0.00 - ETA: 9s - loss: 0.0097 - ETA: 8s - loss: 0.010 - ETA: 8s - loss: 0.010 - ETA: 7s - loss: 0.010 - ETA: 6s - loss: 0.011 - ETA: 6s - loss: 0.011 - ETA: 5s - loss: 0.011 - ETA: 4

1407/1407 [==============================] - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.00 - ETA: 12s - loss: 0.00 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.00 - ETA: 10s - loss: 0.00 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0104 - ETA: 8s - loss: 0.010 - ETA: 8s - loss: 0.010 - ETA: 7s - loss: 0.010 - ETA: 6s - loss: 0.010 - ETA: 6s - loss: 0.010 - ETA: 5s - loss: 0.010 - ETA: 4s - loss: 0.011 - ETA: 4s - loss: 0.011 - ETA: 3s - loss: 0.012 - ETA: 2s - loss: 0.013 - ETA: 2s - loss: 0.014 - ETA: 1s - loss: 0.014 - ETA: 0s - loss: 0.014 - 17s 12ms/step - loss: 0.0143 - val_loss: 0.1815
Epoch 483/500
1407/1407 [==============================] - ETA: 15s - loss: 0.00 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0105 - ETA: 8s - loss: 0.010 - ETA: 7s - loss: 0.010 - ETA: 7s - loss: 0.010 - ETA: 6s - loss: 0.010 - ETA: 5s - loss: 0.010 - ETA: 5

1407/1407 [==============================] - ETA: 15s - loss: 0.00 - ETA: 14s - loss: 0.01 - ETA: 14s - loss: 0.01 - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 10s - loss: 0.01 - ETA: 9s - loss: 0.0111 - ETA: 9s - loss: 0.012 - ETA: 8s - loss: 0.012 - ETA: 7s - loss: 0.013 - ETA: 7s - loss: 0.013 - ETA: 6s - loss: 0.015 - ETA: 5s - loss: 0.016 - ETA: 4s - loss: 0.017 - ETA: 4s - loss: 0.017 - ETA: 3s - loss: 0.017 - ETA: 2s - loss: 0.016 - ETA: 2s - loss: 0.016 - ETA: 1s - loss: 0.016 - ETA: 0s - loss: 0.016 - 17s 12ms/step - loss: 0.0159 - val_loss: 0.1809
Epoch 496/500
1407/1407 [==============================] - ETA: 14s - loss: 0.00 - ETA: 13s - loss: 0.00 - ETA: 13s - loss: 0.00 - ETA: 12s - loss: 0.00 - ETA: 11s - loss: 0.00 - ETA: 11s - loss: 0.00 - ETA: 10s - loss: 0.00 - ETA: 9s - loss: 0.0087 - ETA: 8s - loss: 0.009 - ETA: 8s - loss: 0.011 - ETA: 7s - loss: 0.012 - ETA: 6s - loss: 0.012 - ETA: 6s - loss: 0.013 - ETA: 5s - loss: 0.013 - ETA: 4

c:\software\python3\lib\site-packages\keras\engine\network.py:877: UserWarning: Layer lstm_38 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_37/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_37/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


In [ ]:
# load saved model and train more
bass_x_train, bass_y_train = pickle.load(open('training_set/offspring_bass_data.pkl','rb'))
bass_model = Seq2SeqModel(latent_dim, bass_x_train, bass_x_train)
bass_model.load('models/offspring_bass_model.h5')
bass_model.fit(batch_size, 500)
bass_model.save('models/offspring_bass_model.h5')

In [53]:
'''DRUMS'''
# make model, and train from zero
drums_x_train, drums_y_train = pickle.load(open('training_set/offspring_drums_data.pkl','rb'))
drums_model = Seq2SeqModel(latent_dim, drums_x_train, drums_y_train)
drums_model.fit(batch_size, 500)
drums_model.save('models/offspring_drums_model.h5')

Train on 1332 samples, validate on 333 samples
Epoch 1/500
1332/1332 [==============================] - ETA: 1:36 - loss: 3.509 - ETA: 52s - loss: 3.430 - ETA: 37s - loss: 3.42 - ETA: 29s - loss: 3.30 - ETA: 24s - loss: 3.24 - ETA: 20s - loss: 3.14 - ETA: 17s - loss: 3.08 - ETA: 15s - loss: 2.99 - ETA: 13s - loss: 2.91 - ETA: 11s - loss: 2.85 - ETA: 10s - loss: 2.82 - ETA: 9s - loss: 2.7960 - ETA: 7s - loss: 2.766 - ETA: 6s - loss: 2.739 - ETA: 5s - loss: 2.720 - ETA: 4s - loss: 2.704 - ETA: 3s - loss: 2.676 - ETA: 2s - loss: 2.662 - ETA: 1s - loss: 2.649 - ETA: 0s - loss: 2.629 - 21s 16ms/step - loss: 2.6187 - val_loss: 2.4211
Epoch 2/500
1332/1332 [==============================] - ETA: 12s - loss: 2.41 - ETA: 12s - loss: 2.35 - ETA: 11s - loss: 2.30 - ETA: 10s - loss: 2.33 - ETA: 10s - loss: 2.33 - ETA: 9s - loss: 2.3332 - ETA: 8s - loss: 2.329 - ETA: 8s - loss: 2.348 - ETA: 7s - loss: 2.358 - ETA: 7s - loss: 2.357 - ETA: 6s - loss: 2.368 - ETA: 5s - loss: 2.364 - ETA: 5s - loss: 2.

1332/1332 [==============================] - ETA: 14s - loss: 1.22 - ETA: 13s - loss: 1.17 - ETA: 12s - loss: 1.18 - ETA: 11s - loss: 1.15 - ETA: 10s - loss: 1.13 - ETA: 10s - loss: 1.11 - ETA: 9s - loss: 1.1080 - ETA: 8s - loss: 1.108 - ETA: 7s - loss: 1.105 - ETA: 7s - loss: 1.102 - ETA: 6s - loss: 1.107 - ETA: 5s - loss: 1.111 - ETA: 5s - loss: 1.111 - ETA: 4s - loss: 1.105 - ETA: 3s - loss: 1.107 - ETA: 3s - loss: 1.112 - ETA: 2s - loss: 1.108 - ETA: 1s - loss: 1.107 - ETA: 1s - loss: 1.105 - ETA: 0s - loss: 1.103 - 16s 12ms/step - loss: 1.1043 - val_loss: 1.1327
Epoch 15/500
1332/1332 [==============================] - ETA: 13s - loss: 1.06 - ETA: 12s - loss: 1.01 - ETA: 12s - loss: 1.01 - ETA: 11s - loss: 1.03 - ETA: 10s - loss: 1.05 - ETA: 10s - loss: 1.04 - ETA: 9s - loss: 1.0534 - ETA: 8s - loss: 1.055 - ETA: 7s - loss: 1.035 - ETA: 7s - loss: 1.041 - ETA: 6s - loss: 1.047 - ETA: 5s - loss: 1.046 - ETA: 5s - loss: 1.054 - ETA: 4s - loss: 1.061 - ETA: 3s - loss: 1.067 - ETA: 3s

Epoch 28/500
1332/1332 [==============================] - ETA: 13s - loss: 0.61 - ETA: 12s - loss: 0.61 - ETA: 12s - loss: 0.60 - ETA: 11s - loss: 0.58 - ETA: 10s - loss: 0.57 - ETA: 9s - loss: 0.5691 - ETA: 9s - loss: 0.562 - ETA: 8s - loss: 0.565 - ETA: 7s - loss: 0.559 - ETA: 7s - loss: 0.555 - ETA: 6s - loss: 0.558 - ETA: 5s - loss: 0.559 - ETA: 5s - loss: 0.557 - ETA: 4s - loss: 0.558 - ETA: 3s - loss: 0.559 - ETA: 3s - loss: 0.562 - ETA: 2s - loss: 0.561 - ETA: 1s - loss: 0.563 - ETA: 1s - loss: 0.566 - ETA: 0s - loss: 0.569 - 16s 12ms/step - loss: 0.5697 - val_loss: 0.6047
Epoch 29/500
1332/1332 [==============================] - ETA: 13s - loss: 0.61 - ETA: 12s - loss: 0.55 - ETA: 11s - loss: 0.55 - ETA: 11s - loss: 0.53 - ETA: 10s - loss: 0.54 - ETA: 9s - loss: 0.5471 - ETA: 9s - loss: 0.553 - ETA: 8s - loss: 0.548 - ETA: 7s - loss: 0.546 - ETA: 7s - loss: 0.541 - ETA: 6s - loss: 0.539 - ETA: 5s - loss: 0.540 - ETA: 5s - loss: 0.539 - ETA: 4s - loss: 0.535 - ETA: 3s - loss: 0.

Epoch 42/500
1332/1332 [==============================] - ETA: 13s - loss: 0.29 - ETA: 12s - loss: 0.28 - ETA: 11s - loss: 0.28 - ETA: 11s - loss: 0.27 - ETA: 10s - loss: 0.28 - ETA: 9s - loss: 0.2825 - ETA: 9s - loss: 0.283 - ETA: 8s - loss: 0.284 - ETA: 7s - loss: 0.289 - ETA: 7s - loss: 0.287 - ETA: 6s - loss: 0.289 - ETA: 5s - loss: 0.289 - ETA: 5s - loss: 0.288 - ETA: 4s - loss: 0.289 - ETA: 3s - loss: 0.289 - ETA: 3s - loss: 0.290 - ETA: 2s - loss: 0.288 - ETA: 1s - loss: 0.288 - ETA: 1s - loss: 0.287 - ETA: 0s - loss: 0.287 - 16s 12ms/step - loss: 0.2870 - val_loss: 0.3365
Epoch 43/500
1332/1332 [==============================] - ETA: 13s - loss: 0.28 - ETA: 12s - loss: 0.28 - ETA: 12s - loss: 0.29 - ETA: 11s - loss: 0.28 - ETA: 10s - loss: 0.28 - ETA: 9s - loss: 0.2916 - ETA: 9s - loss: 0.292 - ETA: 8s - loss: 0.290 - ETA: 7s - loss: 0.287 - ETA: 7s - loss: 0.284 - ETA: 6s - loss: 0.282 - ETA: 5s - loss: 0.282 - ETA: 5s - loss: 0.283 - ETA: 4s - loss: 0.280 - ETA: 3s - loss: 0.

Epoch 56/500
1332/1332 [==============================] - ETA: 14s - loss: 0.19 - ETA: 13s - loss: 0.18 - ETA: 13s - loss: 0.18 - ETA: 12s - loss: 0.18 - ETA: 11s - loss: 0.18 - ETA: 10s - loss: 0.18 - ETA: 9s - loss: 0.1864 - ETA: 8s - loss: 0.185 - ETA: 8s - loss: 0.185 - ETA: 7s - loss: 0.183 - ETA: 6s - loss: 0.185 - ETA: 6s - loss: 0.186 - ETA: 5s - loss: 0.185 - ETA: 4s - loss: 0.188 - ETA: 3s - loss: 0.188 - ETA: 3s - loss: 0.187 - ETA: 2s - loss: 0.185 - ETA: 1s - loss: 0.186 - ETA: 1s - loss: 0.187 - ETA: 0s - loss: 0.188 - 16s 12ms/step - loss: 0.1889 - val_loss: 0.2478
Epoch 57/500
1332/1332 [==============================] - ETA: 13s - loss: 0.17 - ETA: 12s - loss: 0.17 - ETA: 11s - loss: 0.17 - ETA: 11s - loss: 0.17 - ETA: 10s - loss: 0.17 - ETA: 9s - loss: 0.1793 - ETA: 9s - loss: 0.182 - ETA: 8s - loss: 0.180 - ETA: 7s - loss: 0.177 - ETA: 7s - loss: 0.178 - ETA: 6s - loss: 0.179 - ETA: 5s - loss: 0.180 - ETA: 5s - loss: 0.181 - ETA: 4s - loss: 0.180 - ETA: 3s - loss: 0.

...

Epoch 448/500
1332/1332 [==============================] - ETA: 13s - loss: 0.02 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0206 - ETA: 9s - loss: 0.020 - ETA: 8s - loss: 0.021 - ETA: 8s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 6s - loss: 0.022 - ETA: 6s - loss: 0.022 - ETA: 5s - loss: 0.023 - ETA: 4s - loss: 0.022 - ETA: 3s - loss: 0.023 - ETA: 3s - loss: 0.023 - ETA: 2s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 0s - loss: 0.023 - 16s 12ms/step - loss: 0.0236 - val_loss: 0.2347
Epoch 449/500
1332/1332 [==============================] - ETA: 13s - loss: 0.02 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0214 - ETA: 9s - loss: 0.021 - ETA: 8s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 6s - loss: 0.021 - ETA: 5s - loss: 0.022 - ETA: 5s - loss: 0.022 - ETA: 4s - loss: 0.022 - ETA: 3s - loss: 

Epoch 462/500
1332/1332 [==============================] - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.01 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0251 - ETA: 8s - loss: 0.024 - ETA: 7s - loss: 0.024 - ETA: 7s - loss: 0.023 - ETA: 6s - loss: 0.024 - ETA: 5s - loss: 0.024 - ETA: 5s - loss: 0.024 - ETA: 4s - loss: 0.024 - ETA: 3s - loss: 0.024 - ETA: 3s - loss: 0.024 - ETA: 2s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 0s - loss: 0.023 - 16s 12ms/step - loss: 0.0240 - val_loss: 0.2298
Epoch 463/500
1332/1332 [==============================] - ETA: 13s - loss: 0.02 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0221 - ETA: 9s - loss: 0.022 - ETA: 8s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 7s - loss: 0.022 - ETA: 6s - loss: 0.021 - ETA: 5s - loss: 0.021 - ETA: 5s - loss: 0.021 - ETA: 4s - loss: 0.021 - ETA: 3s - loss: 

Epoch 476/500
1332/1332 [==============================] - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0225 - ETA: 9s - loss: 0.023 - ETA: 8s - loss: 0.023 - ETA: 7s - loss: 0.023 - ETA: 7s - loss: 0.023 - ETA: 6s - loss: 0.022 - ETA: 5s - loss: 0.022 - ETA: 5s - loss: 0.023 - ETA: 4s - loss: 0.023 - ETA: 3s - loss: 0.023 - ETA: 3s - loss: 0.023 - ETA: 2s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 1s - loss: 0.023 - ETA: 0s - loss: 0.023 - 16s 12ms/step - loss: 0.0236 - val_loss: 0.2329
Epoch 477/500
1332/1332 [==============================] - ETA: 13s - loss: 0.02 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0208 - ETA: 8s - loss: 0.021 - ETA: 8s - loss: 0.020 - ETA: 7s - loss: 0.020 - ETA: 6s - loss: 0.021 - ETA: 6s - loss: 0.021 - ETA: 5s - loss: 0.021 - ETA: 4s - loss: 0.021 - ETA: 4s - loss: 

Epoch 490/500
1332/1332 [==============================] - ETA: 13s - loss: 0.02 - ETA: 12s - loss: 0.01 - ETA: 11s - loss: 0.01 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0201 - ETA: 9s - loss: 0.020 - ETA: 8s - loss: 0.020 - ETA: 7s - loss: 0.019 - ETA: 7s - loss: 0.020 - ETA: 6s - loss: 0.020 - ETA: 5s - loss: 0.020 - ETA: 5s - loss: 0.021 - ETA: 4s - loss: 0.021 - ETA: 3s - loss: 0.021 - ETA: 3s - loss: 0.021 - ETA: 2s - loss: 0.021 - ETA: 1s - loss: 0.021 - ETA: 1s - loss: 0.021 - ETA: 0s - loss: 0.021 - 16s 12ms/step - loss: 0.0218 - val_loss: 0.2334
Epoch 491/500
1332/1332 [==============================] - ETA: 13s - loss: 0.01 - ETA: 12s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 11s - loss: 0.02 - ETA: 10s - loss: 0.02 - ETA: 9s - loss: 0.0209 - ETA: 9s - loss: 0.021 - ETA: 8s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 7s - loss: 0.021 - ETA: 6s - loss: 0.021 - ETA: 5s - loss: 0.021 - ETA: 5s - loss: 0.021 - ETA: 4s - loss: 0.021 - ETA: 3s - loss: 

c:\software\python3\lib\site-packages\keras\engine\network.py:877: UserWarning: Layer lstm_40 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_39/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_39/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


In [ ]:
# load saved model and train more
drums_x_train, drums_y_train = pickle.load(open('training_set/offspring_drums_data.pkl','rb'))
drums_model = Seq2SeqModel(latent_dim, drums_x_train, drums_y_train)
drums_model.load('models/offspring_drums_model.h5')
drums_model.fit(batch_size, 500)
drums_model.save('models/offspring_drums_model.h5')

# generation of music

In [390]:
'''LOAD MODELS'''

# PROGESS BAR
with tqdm(total=100) as pbar:
    
    # GUITAR
    guitar_x_train, guitar_y_train = pickle.load(open('training_set/offspring_guitar_data.pkl','rb'))
    guitar_model = Seq2SeqModel(latent_dim, guitar_x_train, guitar_y_train)
    guitar_model.load('models/offspring_guitar_model.h5')
    pbar.update(25)
    # MELODY
    melody_x_train, melody_y_train = pickle.load(open('training_set/offspring_melody_data.pkl','rb'))
    melody_x_train = Seq2SeqModel(latent_dim, melody_x_train, melody_y_train)
    melody_model.load('models/offspring_melody_model.h5')
    pbar.update(25)
    # BASS
    bass_x_train, bass_y_train = pickle.load(open('training_set/offspring_bass_data.pkl','rb'))
    bass_model = Seq2SeqModel(latent_dim, bass_x_train, bass_y_train)
    bass_model.load('models/offspring_bass_model.h5')
    pbar.update(25)
    # DRUMS
    drums_x_train, drums_y_train = pickle.load(open('training_set/offspring_drums_data.pkl','rb'))
    drums_model = Seq2SeqModel(latent_dim, drums_x_train, drums_y_train)
    drums_model.load('models/offspring_drums_model.h5')
    pbar.update(25)

100%|██████████| 100/100 [02:48<00:00,  1.68s/it]


In [550]:
guitar_x_train, guitar_y_train = pickle.load(open('training_set/offspring_guitar_data.pkl','rb'))
guitar_model = Seq2SeqModel(latent_dim, guitar_x_train, guitar_y_train)
guitar_model.load('models/offspring_guitar_model.h5')

In [ ]:
midi_counter = 0

In [577]:
''' MAKE MULTIINSTRUMENTAL MUSIC !!!'''

# melody type of generation
# Guitar -> Melody 
#        -> Bass   -> Drums
guitar = guitar_model.develop(mode='from_state')

guitar_data = seq_to_numpy(guitar,
                           melody_model.transformer.x_max_seq_length,
                           melody_model.transformer.x_vocab_size,
                           melody_model.transformer.x_transform_dict)
melody = melody_model.predict(guitar_data)[:-1]

guitar_data = seq_to_numpy(guitar,
                           bass_model.transformer.x_max_seq_length,
                           bass_model.transformer.x_vocab_size,
                           bass_model.transformer.x_transform_dict)
bass = bass_model.predict(guitar_data)[:-1]

bass_data = seq_to_numpy(bass,
                           drums_model.transformer.x_max_seq_length,
                           drums_model.transformer.x_vocab_size,
                           drums_model.transformer.x_transform_dict)
drums = drums_model.predict(bass_data)[:-1]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64


In [578]:
'''COMPILE TO MIDI'''
stream_guitar = Stream(first_tick=0, notes=guitar)
stream_melody = Stream(first_tick=0, notes=melody)
stream_bass = Stream(first_tick=0, notes=bass)
stream_drums = Stream(first_tick=0, notes=drums)

generated_midi = MultiTrack()

track_guitar = SingleTrack(name='Guitar',program=29, is_drum=False, stream=stream_guitar)
track_melody = SingleTrack(name='Melody',program=53, is_drum=False, stream=stream_melody)
track_bass = SingleTrack(name='Bass',program=35, is_drum=False, stream=stream_bass)
track_drums = SingleTrack(name='Drums',program=1, is_drum=True, stream=stream_drums)

generated_midi.tracks.append(track_guitar)
generated_midi.tracks.append(track_melody)
generated_midi.tracks.append(track_bass)
generated_midi.tracks.append(track_drums)

generated_midi.save('generated_music/seq2seq_generated_midi_{}_from_state.mid'.format(midi_counter))
midi_counter += 1